In [ ]:
import os


os.chdir("../")


os.getcwd()


'd:\\DA_workspace\\house_price_regressor\\src'

# Thu vien


In [ ]:
import pandas as pd
import numpy as np
from regressor.Mylib import myfuncs
from sklearn.compose import ColumnTransformer
from sklearn.impute import SimpleImputer
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.model_selection import train_test_split
import re
import plotly.express as px
from sklearn.preprocessing import FunctionTransformer

np.set_printoptions(suppress=True)


Doc du lieu


In [ ]:
df = myfuncs.load_python_object("../artifacts/data_ingestion/train_data.pkl")

df.head()


url            id  \
0  https://bj.lianjia.com/chengjiao/BJCP91246118....  BJCP91246118   
1  https://bj.lianjia.com/chengjiao/BJCY84931208....  BJCY84931208   
2  https://bj.lianjia.com/chengjiao/BJFT84407319....  BJFT84407319   
3  https://bj.lianjia.com/chengjiao/101102374986....  101102374986   
4  https://bj.lianjia.com/chengjiao/BJSJ88626256....  BJSJ88626256   

          Lng        Lat            Cid   tradeTime  DOM  followers  \
0  116.360745  40.088084  1111027377581  2016-01-02  1.0          6   
1  116.421749  39.978036  1111027379248  2012-10-31  1.0          0   
2  116.378925  39.845050  1111027378246  2012-05-20  NaN          0   
3  116.501958  39.882586  1111027379326  2017-12-10  5.0          0   
4  116.203052  39.921408  1111027375872  2014-12-19  NaN          3   

   totalPrice  price  ...  buildingType constructionTime renovationCondition  \
0       330.0  35870  ...           4.0             2007                   4   
1       178.0  36349  ...           4.0             1988                   1   
2       310.0  26672  ...           3.0             2006                   1   
3       830.0  60584  ...           4.0             2004                   3   
4       134.0  26678  ...           4.0             1986                   4   

   buildingStructure ladderRatio elevator  fiveYearsProperty subway  district  \
0                  6       0.333      1.0                1.0    1.0         6   
1                  2       0.333      0.0                0.0    1.0         7   
2                  6       1.000      1.0                0.0    1.0         2   
3                  6       0.667      1.0                0.0    1.0         7   
4                  2       0.333      0.0                1.0    0.0         9   

   communityAverage  
0           57479.0  
1           67681.0  
2           64661.0  
3           59213.0  
4           50187.0  

[5 rows x 26 columns]

Kich thuoc


In [ ]:
df.shape


(286965, 26)

# Ti le missing cac cot


In [ ]:
percent_mising = df.isnull().mean() * 100
percent_mising = percent_mising.sort_values(ascending=False)
percent_mising


DOM                    49.513355
buildingType            0.633178
communityAverage        0.146708
subway                  0.008712
fiveYearsProperty       0.008712
elevator                0.008712
bathRoom                0.000000
district                0.000000
ladderRatio             0.000000
buildingStructure       0.000000
renovationCondition     0.000000
constructionTime        0.000000
floor                   0.000000
url                     0.000000
id                      0.000000
drawingRoom             0.000000
livingRoom              0.000000
square                  0.000000
price                   0.000000
totalPrice              0.000000
followers               0.000000
tradeTime               0.000000
Cid                     0.000000
Lat                     0.000000
Lng                     0.000000
kitchen                 0.000000
dtype: float64

Cot DOM co ti le missing la 49% -> loai bo cot nay


In [ ]:
df = df.drop(columns=["DOM"])
df.columns


Index(['url', 'id', 'Lng', 'Lat', 'Cid', 'tradeTime', 'followers',
       'totalPrice', 'price', 'square', 'livingRoom', 'drawingRoom', 'kitchen',
       'bathRoom', 'floor', 'buildingType', 'constructionTime',
       'renovationCondition', 'buildingStructure', 'ladderRatio', 'elevator',
       'fiveYearsProperty', 'subway', 'district', 'communityAverage'],
      dtype='object')

Kich thuoc con lai


In [ ]:
df.shape


(286965, 25)

In [ ]:
df["buildingType"].unique()


array([4.   , 3.   , 1.   , 2.   ,   nan, 0.125, 0.5  , 0.25 , 0.667,
       0.048, 0.333, 0.375, 0.429])

# Y nghia cac cot

| Cot                 | Y nghia                                                                          | Don vi | Phan loai  |
| ------------------- | -------------------------------------------------------------------------------- | ------ | ---------- |
| **url**             |                                                                                  | none   |            |
| **id**              |                                                                                  | none   | Nominal    |
| Lng                 | Kinh do                                                                          | none   | Numeric    |
| Lat                 | Vi do                                                                            | none   | Numeric    |
| **Cid**             | Ko co y nghia ro rang                                                            | none   | Numeric    |
| tradeTime           | Thoi gian giao dich                                                              | none   | Date       |
| followers           | So nguoi theo doi                                                                | none   | Numeric    |
| **totalPrice**      |                                                                                  | none   | Numeric    |
| _price_             | **Cot muc tieu **                                                                | none   | Numeric    |
| square              | Dien tich                                                                        | none   | Numeric    |
| livingRoom          | So phong khach                                                                   | none   | NumericCat |
| drawingRoom         | So phong ve                                                                      | none   | NumericCat |
| kitchen             | So nha bep                                                                       | none   | NumericCat |
| bathRoom            | So phong tam                                                                     | none   | NumericCat |
| **floor**           | So tang nha, **can fix loi**                                                     | none   | NumericCat |
| buildingType        | Loai nha                                                                         | none   | nominal    |
| constructionTime    | Thoi gian xay dung                                                               | none   | NumericCat |
| renovationCondition | Tinh trang sua chua                                                              | none   | NumericCat |
| buildingStructure   | Cau truc xay dung                                                                | none   | nominal    |
| ladderRatio         | tỷ lệ giữa số lượng cư dân trên một tầng và số lượng thang máy trong một tòa nhà | none   | Numeric    |
| **elevator**        | so thang may                                                                     | none   | Numeric    |
| fiveYearsProperty   | 1 -> bds moi, 0 -> bds cu                                                        | none   | nominal    |
| subway              | co gan subway khong                                                              | none   | binary     |
| district            | o huyen nao                                                                      | none   | nominal    |
| communityAverage    | gia nha trung binh trong cong dong                                               | none   | numeric    |


Xoa cac cot khong can thiet


In [ ]:
df = df.drop(
    columns=[
        "url",
        "id",
        "Cid",
        "totalPrice",
        "floor",
        "elevator",
    ]
)

df.head()


Lng        Lat   tradeTime  followers  price  square livingRoom  \
0  116.360745  40.088084  2016-01-02          6  35870   92.00          2   
1  116.421749  39.978036  2012-10-31          0  36349   48.97          2   
2  116.378925  39.845050  2012-05-20          0  26672  116.23          2   
3  116.501958  39.882586  2017-12-10          0  60584  137.00          3   
4  116.203052  39.921408  2014-12-19          3  26678   50.23          2   

  drawingRoom  kitchen bathRoom  buildingType constructionTime  \
0           2        1        1           4.0             2007   
1           1        1        1           4.0             1988   
2           1        1        2           3.0             2006   
3           1        1        2           4.0             2004   
4           1        1        1           4.0             1986   

   renovationCondition  buildingStructure  ladderRatio  fiveYearsProperty  \
0                    4                  6        0.333                1.0   
1                    1                  2        0.333                0.0   
2                    1                  6        1.000                0.0   
3                    3                  6        0.667                0.0   
4                    4                  2        0.333                1.0   

   subway  district  communityAverage  
0     1.0         6           57479.0  
1     1.0         7           67681.0  
2     1.0         2           64661.0  
3     1.0         7           59213.0  
4     0.0         9           50187.0

# Doi ten cot


In [ ]:
df.columns


Index(['Lng', 'Lat', 'tradeTime', 'followers', 'price', 'square', 'livingRoom',
       'drawingRoom', 'kitchen', 'bathRoom', 'buildingType',
       'constructionTime', 'renovationCondition', 'buildingStructure',
       'ladderRatio', 'fiveYearsProperty', 'subway', 'district',
       'communityAverage'],
      dtype='object')

In [ ]:
rename_dict = {
    "Lng": "Lng_num",
    "Lat": "Lat_num",
    "tradeTime": "tradeTime_date",
    "followers": "followers_num",
    "square": "square_num",
    "livingRoom": "livingRoom_numcat",
    "drawingRoom": "drawingRoom_numcat",
    "kitchen": "kitchen_numcat",
    "bathRoom": "bathRoom_numcat",
    "buildingType": "buildingType_nom",
    "constructionTime": "constructionTime_numcat",
    "renovationCondition": "renovationCondition_numcat",
    "buildingStructure": "buildingStructure_nom",
    "ladderRatio": "ladderRatio_num",
    "fiveYearsProperty": "fiveYearsProperty_nom",
    "subway": "subway_bin",
    "district": "district_nom",
    "communityAverage": "communityAverage_num",
}


df = df.rename(columns=rename_dict)

df.head()


Lng_num    Lat_num tradeTime_date  followers_num  price  square_num  \
0  116.360745  40.088084     2016-01-02              6  35870       92.00   
1  116.421749  39.978036     2012-10-31              0  36349       48.97   
2  116.378925  39.845050     2012-05-20              0  26672      116.23   
3  116.501958  39.882586     2017-12-10              0  60584      137.00   
4  116.203052  39.921408     2014-12-19              3  26678       50.23   

  livingRoom_numcat drawingRoom_numcat  kitchen_numcat bathRoom_numcat  \
0                 2                  2               1               1   
1                 2                  1               1               1   
2                 2                  1               1               2   
3                 3                  1               1               2   
4                 2                  1               1               1   

   buildingType_nom constructionTime_numcat  renovationCondition_numcat  \
0               4.0                    2007                           4   
1               4.0                    1988                           1   
2               3.0                    2006                           1   
3               4.0                    2004                           3   
4               4.0                    1986                           4   

   buildingStructure_nom  ladderRatio_num  fiveYearsProperty_nom  subway_bin  \
0                      6            0.333                    1.0         1.0   
1                      2            0.333                    0.0         1.0   
2                      6            1.000                    0.0         1.0   
3                      6            0.667                    0.0         1.0   
4                      2            0.333                    1.0         0.0   

   district_nom  communityAverage_num  
0             6               57479.0  
1             7               67681.0  
2             2               64661.0  
3             7               59213.0  
4             9               50187.0

Bo cot datetime di


In [ ]:
df = df.drop(columns=["tradeTime_date"])
df.columns


Index(['Lng_num', 'Lat_num', 'followers_num', 'price', 'square_num',
       'livingRoom_numcat', 'drawingRoom_numcat', 'kitchen_numcat',
       'bathRoom_numcat', 'buildingType_nom', 'constructionTime_numcat',
       'renovationCondition_numcat', 'buildingStructure_nom',
       'ladderRatio_num', 'fiveYearsProperty_nom', 'subway_bin',
       'district_nom', 'communityAverage_num'],
      dtype='object')

# Chuyen cac cot numeric, numericCat, binary, nominal, ordinal, target ve dung vi tri


In [ ]:
cols = pd.Series(df.columns)
numeric_cols = cols[cols.str.endswith("num")].tolist()
numericCat_cols = cols[cols.str.endswith("numcat")].tolist()
binary_cols = cols[cols.str.endswith("bin")].tolist()
nominal_cols = cols[cols.str.endswith("nom")].tolist()
ordinal_cols = cols[cols.str.endswith("ord")].tolist()


target_col = "price"


df = df[
    numeric_cols
    + numericCat_cols
    + binary_cols
    + nominal_cols
    + ordinal_cols
    + [target_col]
]


df.head()


Lng_num    Lat_num  followers_num  square_num  ladderRatio_num  \
0  116.360745  40.088084              6       92.00            0.333   
1  116.421749  39.978036              0       48.97            0.333   
2  116.378925  39.845050              0      116.23            1.000   
3  116.501958  39.882586              0      137.00            0.667   
4  116.203052  39.921408              3       50.23            0.333   

   communityAverage_num livingRoom_numcat drawingRoom_numcat  kitchen_numcat  \
0               57479.0                 2                  2               1   
1               67681.0                 2                  1               1   
2               64661.0                 2                  1               1   
3               59213.0                 3                  1               1   
4               50187.0                 2                  1               1   

  bathRoom_numcat constructionTime_numcat  renovationCondition_numcat  \
0               1                    2007                           4   
1               1                    1988                           1   
2               2                    2006                           1   
3               2                    2004                           3   
4               1                    1986                           4   

   subway_bin  buildingType_nom  buildingStructure_nom  fiveYearsProperty_nom  \
0         1.0               4.0                      6                    1.0   
1         1.0               4.0                      2                    0.0   
2         1.0               3.0                      6                    0.0   
3         1.0               4.0                      6                    0.0   
4         0.0               4.0                      2                    1.0   

   district_nom  price  
0             6  35870  
1             7  36349  
2             2  26672  
3             7  60584  
4             9  26678

# Kiem tra kieu du lieu cac cot


In [ ]:
df.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 286965 entries, 0 to 286964
Data columns (total 18 columns):
 #   Column                      Non-Null Count   Dtype  
---  ------                      --------------   -----  
 0   Lng_num                     286965 non-null  float64
 1   Lat_num                     286965 non-null  float64
 2   followers_num               286965 non-null  int64  
 3   square_num                  286965 non-null  float64
 4   ladderRatio_num             286965 non-null  float64
 5   communityAverage_num        286544 non-null  float64
 6   livingRoom_numcat           286965 non-null  object 
 7   drawingRoom_numcat          286965 non-null  object 
 8   kitchen_numcat              286965 non-null  int64  
 9   bathRoom_numcat             286965 non-null  object 
 10  constructionTime_numcat     286965 non-null  object 
 11  renovationCondition_numcat  286965 non-null  int64  
 12  subway_bin                  286940 non-null  float64
 13  buildingType_n

SAI

- livingRoom_numcat
- drawingRoom_numcat
- bathRoom_numcat
- constructionTime_numcat
- subway_bin
- buildingType_nom
- buildingStructure_nom
- fiveYearsProperty_nom
- district_nom


# Chuyen doi kieu du lieu (SAI) -> kieu du lieu mong muon + nan


## Cot livingRoom_num


In [ ]:
col_name = "livingRoom_numcat"

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{int, str}

In [ ]:
value_type_str = value_not_missing[
    value_not_missing.apply(lambda x: isinstance(x, str))
]

value_type_str.unique()


array(['2', '3', '1', '4', '5', '6', '0', '7', '#NAME?', '9', '8'],
      dtype=object)

In [ ]:
value_nan = value_type_str[value_type_str == "#NAME?"]
value_nan = value_nan.replace({"#NAME?": np.nan})
value_type_str = value_type_str[~value_type_str.index.isin(value_nan.index)]
value_type_str = value_type_str.astype("int")

value_type_str.unique(), value_nan.unique()


C:\Users\AdminPc\AppData\Local\Temp\ipykernel_392\3038062162.py:2: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  value_nan = value_nan.replace({"#NAME?": np.nan})


(array([2, 3, 1, 4, 5, 6, 0, 7, 9, 8]), array([nan]))

In [ ]:
df.loc[value_nan.index, col_name] = value_nan
df.loc[value_type_str.index, col_name] = value_type_str

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{int}

## Cot drawingRoom_numcat


In [ ]:
col_name = "drawingRoom_numcat"

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{int, str}

In [ ]:
value_type_str = value_not_missing[
    value_not_missing.apply(lambda x: isinstance(x, str))
]

value_type_str.unique()


array(['2', '1', '0', '3', '4', '5', 'ÖÐ 14', 'ÖÐ 6', 'ÖÐ 22', '¸ß 12',
       'µÍ 6', 'ÖÐ 16', 'ÖÐ 15', 'µÍ 15', 'µ× 11', 'µÍ 16', 'ÖÐ 24',
       'µ× 20', '¸ß 6', 'µ× 28', '¶¥ 6', '¸ß 14'], dtype=object)

In [ ]:
value_type_int = value_type_str[
    value_type_str.apply(lambda x: myfuncs.is_integer_str(x))
]
value_type_int = value_type_int.astype("int")

value_not_type_int = value_type_str[~value_type_str.index.isin(value_type_int.index)]
value_not_type_int = value_not_type_int.str.split(" ").str[1]
value_not_type_int.unique()


array(['14', '6', '22', '12', '16', '15', '11', '24', '20', '28'],
      dtype=object)

In [ ]:
value_not_type_int = value_not_type_int.astype("int")

df.loc[value_type_int.index, col_name] = value_type_int
df.loc[value_not_type_int.index, col_name] = value_not_type_int

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{int}

## Cot bathRoom_numcat


In [ ]:
col_name = "bathRoom_numcat"

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{int, str}

In [ ]:
value_type_str = value_not_missing[
    value_not_missing.apply(lambda x: isinstance(x, str))
]

value_type_str.unique()


array(['1', '2', '4', '3', '0', '5', '2003', '7', 'Î´Öª'], dtype=object)

In [ ]:
value_type_int = value_type_str[
    value_type_str.apply(lambda x: myfuncs.is_integer_str(x))
]
value_type_int = value_type_int.astype("int")

value_not_type_int = value_type_str[~value_type_str.index.isin(value_type_int.index)]
value_not_type_int[:] = np.nan


df.loc[value_type_int.index, col_name] = value_type_int
df.loc[value_not_type_int.index, col_name] = value_not_type_int
value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{int}

## Cot constructionTime_numcat


In [ ]:
col_name = "constructionTime_numcat"

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{str}

In [ ]:
value_not_missing.unique()


array(['2007', '1988', '2006', '2004', '1986', '1989', '1980', '1979',
       '1981', '1987', '1998', '2011', '2009', '2010', '1990', '1991',
       '1997', '2002', '1993', '2008', '2000', '2003', 'Î´Öª', '2005',
       '2001', '1999', '1984', '1994', '1985', '2014', '1995', '2013',
       '1992', '1978', '1996', '1982', '2012', '1967', '1983', '1977',
       '2015', '1974', '1976', '1975', '1970', '1960', '1955', '1963',
       '1965', '1958', '1964', '1962', '1973', '1956', '1966', '1959',
       '2016', '1969', '1971', '1954', '1953', '1972', '1957', '1950',
       '1961', '1', '1944', '0', '1952', '1968', '1914', '1934', '1906',
       '1933'], dtype=object)

In [ ]:
value_type_int = value_not_missing[
    value_not_missing.apply(lambda x: myfuncs.is_integer_str(x))
]
value_type_int = value_type_int.astype("int")

value_not_type_int = value_not_missing[
    ~value_not_missing.index.isin(value_type_int.index)
]
value_not_type_int[:] = np.nan


df.loc[value_type_int.index, col_name] = value_type_int
df.loc[value_not_type_int.index, col_name] = value_not_type_int
value_not_missing = df[col_name][~pd.isnull(df[col_name])]
set(map(type, value_not_missing))


{int}

## Cot subway_bin


In [ ]:
col_name = "subway_bin"

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{float}

In [ ]:
value_not_missing.unique()


array([1., 0.])

## Cot buildingType_nom


In [ ]:
col_name = "buildingType_nom"

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{float}

In [ ]:
value_not_missing.unique()


array([4.   , 3.   , 1.   , 2.   , 0.125, 0.5  , 0.25 , 0.667, 0.048,
       0.333, 0.375, 0.429])

## Cot buildingStructure_nom


In [ ]:
col_name = "buildingStructure_nom"

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{int}

In [ ]:
value_not_missing.unique()


array([6, 2, 4, 1, 3, 5, 0], dtype=int64)

## Cot fiveYearsProperty_nom


In [ ]:
col_name = "fiveYearsProperty_nom"

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{float}

In [ ]:
value_not_missing.unique()


array([1., 0.])

## Cot district_nom


In [ ]:
col_name = "district_nom"

value_not_missing = df[col_name][~pd.isnull(df[col_name])]

set(map(type, value_not_missing))


{int}

In [ ]:
value_not_missing.unique()


array([ 6,  7,  2,  9,  1,  8, 10,  4, 11, 13,  3, 12,  5], dtype=int64)

# Kiem tra noi dung cac cot

## Cot numeric


In [ ]:
df[numeric_cols] = df[numeric_cols].astype("float")
df[numeric_cols].describe().loc[["min", "max", "mean"]]


Lng_num    Lat_num  followers_num  square_num  ladderRatio_num  \
min   116.072514  39.627030       0.000000     6.90000     0.000000e+00   
max   116.732378  40.252758    1143.000000  1745.50000     1.000940e+07   
mean  116.418532  39.949528      16.735881    83.25328     3.526095e+01   

      communityAverage_num  
min           10847.000000  
max          183109.000000  
mean          63649.680772

## Cot numericCat


In [ ]:
min_of_cols = df[numericCat_cols].min().to_frame(name="min")
max_of_cols = df[numericCat_cols].max().to_frame(name="max")
median_of_cols = df[numericCat_cols].quantile([0.5]).T.rename(columns={0.5: "median"})

result = pd.concat([min_of_cols, max_of_cols, median_of_cols], axis=1).T

result


livingRoom_numcat drawingRoom_numcat kitchen_numcat bathRoom_numcat  \
min                    0                  0              0               0   
max                    9                 28              4            2011   
median               2.0                1.0            1.0             1.0   

       constructionTime_numcat renovationCondition_numcat  
min                          0                          0  
max                       2016                          4  
median                  2001.0                        3.0

Cot constructionTime_num co min = 0 -> vo li


In [ ]:
df["constructionTime_numcat"].unique()


array([2007, 1988, 2006, 2004, 1986, 1989, 1980, 1979, 1981, 1987, 1998,
       2011, 2009, 2010, 1990, 1991, 1997, 2002, 1993, 2008, 2000, 2003,
       nan, 2005, 2001, 1999, 1984, 1994, 1985, 2014, 1995, 2013, 1992,
       1978, 1996, 1982, 2012, 1967, 1983, 1977, 2015, 1974, 1976, 1975,
       1970, 1960, 1955, 1963, 1965, 1958, 1964, 1962, 1973, 1956, 1966,
       1959, 2016, 1969, 1971, 1954, 1953, 1972, 1957, 1950, 1961, 1,
       1944, 0, 1952, 1968, 1914, 1934, 1906, 1933], dtype=object)

Co 2 gia tri bat thuong: 0, 1 -> chuyen ve nan


In [ ]:
df["constructionTime_numcat"] = df["constructionTime_numcat"].replace(
    {
        0: np.nan,
        1: np.nan,
    }
)

df["constructionTime_numcat"].unique()


C:\Users\AdminPc\AppData\Local\Temp\ipykernel_392\1812380787.py:1: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df["constructionTime_numcat"] = df["constructionTime_numcat"].replace(


array([2007., 1988., 2006., 2004., 1986., 1989., 1980., 1979., 1981.,
       1987., 1998., 2011., 2009., 2010., 1990., 1991., 1997., 2002.,
       1993., 2008., 2000., 2003.,   nan, 2005., 2001., 1999., 1984.,
       1994., 1985., 2014., 1995., 2013., 1992., 1978., 1996., 1982.,
       2012., 1967., 1983., 1977., 2015., 1974., 1976., 1975., 1970.,
       1960., 1955., 1963., 1965., 1958., 1964., 1962., 1973., 1956.,
       1966., 1959., 2016., 1969., 1971., 1954., 1953., 1972., 1957.,
       1950., 1961., 1944., 1952., 1968., 1914., 1934., 1906., 1933.])

Cot ladderRatio_num co max = 10009400, trong khi mean = 35


In [ ]:
fig = px.box(y=df["ladderRatio_num"])
fig.show()


Thay the cac gia tri outlier phia tren thanh nan


In [ ]:
col_name = "ladderRatio_num"
nguong = np.percentile(df[col_name], 75) + 1.5 * (
    np.percentile(df[col_name], 75) - np.percentile(df[col_name], 25)
)
outliers = df[col_name][df[col_name] > nguong]
df.loc[outliers.index, col_name] = np.nan

fig = px.box(y=df["ladderRatio_num"])
fig.show()


## Cot binary


In [ ]:
for col in binary_cols:
    print(f"{col} -> {df[col].unique().tolist()}")


subway_bin -> [1.0, 0.0, nan]


In [ ]:
df[binary_cols] = df[binary_cols].astype("string")


In [ ]:
for col in binary_cols:
    print(f"{col} -> {df[col].unique().tolist()}")


subway_bin -> ['1.0', '0.0', <NA>]


## Cot nominal


In [ ]:
for col in nominal_cols:
    print(f"{col} -> {df[col].unique().tolist()}")


buildingType_nom -> [4.0, 3.0, 1.0, 2.0, nan, 0.125, 0.5, 0.25, 0.667, 0.048, 0.333, 0.375, 0.429]
buildingStructure_nom -> [6, 2, 4, 1, 3, 5, 0]
fiveYearsProperty_nom -> [1.0, 0.0, nan]
district_nom -> [6, 7, 2, 9, 1, 8, 10, 4, 11, 13, 3, 12, 5]


In [ ]:
df[nominal_cols] = df[nominal_cols].astype("string")


## Cot ordinal


In [ ]:
for col in ordinal_cols:
    print(f"{col} -> {df[col].unique().tolist()}")


## Cot target


In [ ]:
df[target_col].describe()


count    286965.000000
mean      43515.315805
std       21700.991600
min           1.000000
25%       28044.000000
50%       38723.000000
75%       53792.000000
max      156250.000000
Name: price, dtype: float64

Gia tri min = 1 -> khong the nho vay duoc


In [ ]:
fig = px.box(y=df[target_col])

fig.show()


# Fill missing value


In [ ]:
df = df.applymap(lambda x: np.nan if x is pd.NA else x)

cat_cols = binary_cols + nominal_cols + ordinal_cols


preprocessor = ColumnTransformer(
    transformers=[
        ("num", SimpleImputer(strategy="mean"), numeric_cols),
        ("numCat", SimpleImputer(strategy="most_frequent"), numericCat_cols),
        ("cat", SimpleImputer(strategy="most_frequent"), cat_cols),
        ("target", SimpleImputer(strategy="mean"), [target_col]),
    ]
)

df_filled = preprocessor.fit_transform(df)


df_filled = pd.DataFrame(
    df_filled, columns=numeric_cols + numericCat_cols + cat_cols + [target_col]
)


# Luu preprocessor lai


folder = "../artifacts/data_correction"


os.makedirs(folder, exist_ok=True)


myfuncs.save_python_object(
    file_path=os.path.join(folder, "missing_value_handler.pkl"), obj=preprocessor
)


df_filled.head()


C:\Users\AdminPc\AppData\Local\Temp\ipykernel_392\728170231.py:1: FutureWarning:

DataFrame.applymap has been deprecated. Use DataFrame.map instead.



Lng_num    Lat_num followers_num square_num ladderRatio_num  \
0  116.360745  40.088084           6.0       92.0           0.333   
1  116.421749  39.978036           0.0      48.97           0.333   
2  116.378925   39.84505           0.0     116.23        0.364061   
3  116.501958  39.882586           0.0      137.0           0.667   
4  116.203052  39.921408           3.0      50.23           0.333   

  communityAverage_num livingRoom_numcat drawingRoom_numcat kitchen_numcat  \
0              57479.0               2.0                2.0            1.0   
1              67681.0               2.0                1.0            1.0   
2              64661.0               2.0                1.0            1.0   
3              59213.0               3.0                1.0            1.0   
4              50187.0               2.0                1.0            1.0   

  bathRoom_numcat constructionTime_numcat renovationCondition_numcat  \
0             1.0                  2007.0                        4.0   
1             1.0                  1988.0                        1.0   
2             2.0                  2006.0                        1.0   
3             2.0                  2004.0                        3.0   
4             1.0                  1986.0                        4.0   

  subway_bin buildingType_nom buildingStructure_nom fiveYearsProperty_nom  \
0        1.0              4.0                     6                   1.0   
1        1.0              4.0                     2                   0.0   
2        1.0              3.0                     6                   0.0   
3        1.0              4.0                     6                   0.0   
4        0.0              4.0                     2                   1.0   

  district_nom    price  
0            6  35870.0  
1            7  36349.0  
2            2  26672.0  
3            7  60584.0  
4            9  26678.0

# Chuyen doi ve dung kieu du lieu


In [ ]:
df_filled[numeric_cols + numericCat_cols] = df_filled[
    numeric_cols + numericCat_cols
].astype("float")


df_filled[cat_cols] = df_filled[cat_cols].astype("category")



df_filled[target_col] = df_filled[target_col].astype("float")

df_filled.info()


<class 'pandas.core.frame.DataFrame'>
RangeIndex: 286965 entries, 0 to 286964
Data columns (total 18 columns):
 #   Column                      Non-Null Count   Dtype   
---  ------                      --------------   -----   
 0   Lng_num                     286965 non-null  float64 
 1   Lat_num                     286965 non-null  float64 
 2   followers_num               286965 non-null  float64 
 3   square_num                  286965 non-null  float64 
 4   ladderRatio_num             286965 non-null  float64 
 5   communityAverage_num        286965 non-null  float64 
 6   livingRoom_numcat           286965 non-null  float64 
 7   drawingRoom_numcat          286965 non-null  float64 
 8   kitchen_numcat              286965 non-null  float64 
 9   bathRoom_numcat             286965 non-null  float64 
 10  constructionTime_numcat     286965 non-null  float64 
 11  renovationCondition_numcat  286965 non-null  float64 
 12  subway_bin                  286965 non-null  category
 13 

# Thay doi thu tu cac label cho cac cot ordinal va binary


In [ ]:
ord_values_dict = {"subway_bin": ["0.0", "1.0"]}

for col, value in ord_values_dict.items():
    df_filled[col] = df_filled[col].cat.reorder_categories(value, ordered=True)


# Check duplicates


In [ ]:
any(df_filled.duplicated())


True

Ti le duplicates


In [ ]:
len(df_filled[df_filled.duplicated()]) / len(df_filled) * 100


0.09339118010907253

In [ ]:
df_filled = df_filled.drop_duplicates().reset_index(drop=True)
df_filled.shape


(286697, 18)

Chia thanh tap train va tap val


In [ ]:
df_train, df_val = train_test_split(df_filled, test_size=0.1, random_state=42)

myfuncs.save_python_object(os.path.join(folder, "train_data.pkl"), df_train)
myfuncs.save_python_object(os.path.join(folder, "val_data.pkl"), df_val)
